# Benchmarks

In [1]:
# the notebook imports
import matplotlib.pyplot as plt
import numpy as np
# this is the convenience function
from autokoopman import auto_koopman
# for a complete example, let's create an example dataset using an included benchmark system
from autokoopman.benchmark import bio2, fhn, lalo20, prde20, robe21, spring, pendulum
from glop import Glop
import random
import copy

from sklearn.metrics import mean_squared_error
import statistics
import os
import csv
import time

In [2]:
benches = [bio2.Bio2(), fhn.FitzHughNagumo(), lalo20.LaubLoomis(), pendulum.PendulumWithInput(beta=0.05), prde20.ProdDestr(), robe21.RobBench(), spring.Spring()]

In [3]:
def get_training_data(bench, param_dict):
    init_states = get_init_states(bench, param_dict["train_size"])
    if bench._input_vars:
        params = np.random.rand(param_dict["train_size"], 3) * 2 - 1
        steps = [make_input_step(*p, bench.teval) for p in params]
        training_data = bench.solve_ivps(initial_states=init_states, inputs=steps, teval=bench.teval)
    else:
        training_data = bench.solve_ivps(initial_states=init_states,tspan=[0.0, 10.0], 
                                         sampling_period=param_dict["samp_period"])
        
    return training_data

In [4]:
def get_init_states(bench, size, init_seed=0):
    if hasattr(bench, 'init_constrs'):
        init_states = []
        for i in range(size):
            init_state_dict = glop_init_states(bench, i+init_seed)
            init_state = []
            for name in bench.names:
                init_state.append(init_state_dict[name])
            init_states.append(init_state)
        init_states = np.array(init_states)  
    else:
        init_states = np.random.uniform(low=bench.init_set_low, 
                    high=bench.init_set_high, size=(size, len(bench.names)))
        
    print(init_states)
    return init_states

In [5]:
def glop_init_states(bench, seed):    
    constrs = []
    for constr in bench.init_constrs:
        constrs.append(constr)
    for i, (name, init_low, init_high) in enumerate(zip(bench.names, bench.init_set_low, bench.init_set_high)):
        low_constr = f"{name} >= {init_low}"
        high_constr = f"{name} <= {init_high}"
        constrs.extend([low_constr, high_constr])
        
    glop = Glop(bench.names, constrs)
    pop_item = random.randrange(len(bench.names))
    names, init_set_low, init_set_high = copy.deepcopy(bench.names), copy.deepcopy(bench.init_set_low), copy.deepcopy(bench.init_set_high)
    names.pop(pop_item)
    init_set_low.pop(pop_item)
    init_set_high.pop(pop_item)
    for i, (name, init_low, init_high) in enumerate(zip(names, init_set_low, init_set_high)):
        glop.add_tend_value_obj_fn(name, [init_low, init_high], seed+i)
    
    glop.minimize()

    sol_dict = glop.get_all_sols()    
    return sol_dict

In [6]:
def get_trajectories(bench, iv, samp_period):
    # get the model from the experiment results
    model = experiment_results['tuned_model']

    if bench._input_vars:
        test_inp = np.sin(np.linspace(0, 10, 200))

        # simulate using the learned model
        trajectory = model.solve_ivp(
            initial_state=iv,
            inputs=test_inp,
            teval=bench.teval,
        )
        # simulate the ground truth for comparison
        true_trajectory = bench.solve_ivp(
            initial_state=iv,
            inputs=test_inp,
            teval=bench.teval,
        )
        
    else:
        # simulate using the learned model
        trajectory = model.solve_ivp(
            initial_state=iv,
            tspan=(0.0, 10.0),
            sampling_period=samp_period
        )
        # simulate the ground truth for comparison
        true_trajectory = bench.solve_ivp(
            initial_state=iv,
            tspan=(0.0, 10.0),
            sampling_period=samp_period
        )
    
    return trajectory, true_trajectory

In [7]:
def test_trajectories(bench, num_tests, samp_period):
    mses = []
    for j in range(num_tests):
        iv = get_init_states(bench, 1, j+10000)[0]
        trajectory, true_trajectory = get_trajectories(bench, iv, samp_period)
        mse = mean_squared_error(trajectory.states.T, true_trajectory.states.T)
        mses.append(mse)
            
    return mses

In [8]:
def make_input_step(duty, on_amplitude, off_amplitude, teval):
    """produce a step response input signal for the pendulum"""
    length = len(teval)
    inp = np.zeros((length,))
    phase_idx = int(length * duty)
    inp[:phase_idx] = on_amplitude
    inp[phase_idx:] = off_amplitude
    return inp

In [9]:
def store_data(bench_name, time_taken, mse):
    if not os.path.exists('data'):
        os.makedirs('data')
        
    with open('data/benches', 'a') as f:
        writer = csv.writer(f)
        row = [bench_name, time_taken, mse]
        writer.writerow(row)
              

In [10]:
def plot(trajectory, true_trajectory):
    plt.figure(figsize=(10, 6))
    # plot the results
    #plt.plot(true_trajectory.states[:, 5])
    plt.plot(trajectory.states.T[0], trajectory.states.T[1],label='Trajectory Prediction')
    plt.plot(true_trajectory.states.T[0], true_trajectory.states.T[1],label='Ground Truth')

    plt.xlabel("$x_1$")
    plt.ylabel("$x_2$")
    plt.grid()
    plt.legend()
    plt.title("Bio2 Test Trajectory Plot")
    plt.show()

In [11]:
for bench in benches:
    np.random.seed(0)
    param_dict = {"train_size":10,"samp_period":0.1,"obs_type":"deep","opt":"grid","n_obs":200,
                  "grid_param_slices":5,"n_splits":5,"rank":(1, 200, 40)}
    start = time.time()
    # generate training data
    print("traininggggg:")
    training_data = get_training_data(bench, param_dict)
    # learn model from data
    experiment_results = auto_koopman(
        training_data,          # list of trajectories
        sampling_period=param_dict["samp_period"],    # sampling period of trajectory snapshots
        obs_type=param_dict["obs_type"],         # use Random Fourier Features Observables
        opt=param_dict["opt"],             # grid search to find best hyperparameters
        n_obs=param_dict["n_obs"],              # maximum number of observables to try
        max_opt_iter=200,       # maximum number of optimization iterations
        grid_param_slices=param_dict["grid_param_slices"],# for grid search, number of slices for each parameter
        n_splits=param_dict["n_splits"],             # k-folds validation for tuning, helps stabilize the scoring
        rank=param_dict["rank"]       # rank range (start, stop, step) DMD hyperparameter
    )

    print("testing:")
    mses = test_trajectories(bench, 10, param_dict["samp_period"])

    end = time.time()       
    time_taken = round(end - start, 3)
    print("The average mean square error is ", statistics.mean(mses))

    store_data(bench.name, time_taken, statistics.mean(mses))

traininggggg:
[[1.00097627 1.00430379 1.00205527 1.00089766 0.9984731  1.00291788
  0.99875174 1.00783546 1.00927326]
 [0.99766883 1.0058345  1.0005779  1.00136089 1.00851193 0.99142072
  0.99174259 0.99040437 1.0066524 ]
 [1.00556314 1.00740024 1.00957237 1.00598317 0.99922959 1.00561058
  0.99236549 1.00279842 0.99286707]
 [1.00889338 1.00043697 0.99829324 0.99529111 1.00548467 0.99912301
  1.00136868 0.9903758  1.00235271]
 [1.00224191 1.00233868 1.00887496 1.00363641 0.99719016 0.99874064
  1.00395262 0.99120451 1.00333533]
 [1.00341276 0.99420765 0.99257853 0.99630857 0.99727422 1.00140394
  0.99877203 1.00976748 0.9920409 ]
 [0.99417754 0.99322619 1.00306217 0.99506583 0.99932622 0.99488851
  0.99317939 0.9922075  1.00312659]
 [0.99276366 0.99393165 0.9973745  1.00641986 0.99194203 1.0067589
  0.99192197 1.00952919 0.99937302]
 [1.00953522 1.00209691 1.00478527 0.99078376 0.99565614 0.99240393
  0.9959228  0.99237455 0.99635966]
 [0.99828526 0.99128295 1.00384944 1.00133203 0.995

100%|████████████████████████████████████████| 500/500 [00:03<00:00, 158.68it/s]

100%|████████████████████████████████████████| 500/500 [00:03<00:00, 158.37it/s]

100%|████████████████████████████████████████| 500/500 [00:03<00:00, 160.17it/s]

  6%|██▌                                      | 32/500 [00:00<00:02, 158.86it/s]


100%|████████████████████████████████████████| 500/500 [00:03<00:00, 162.39it/s]

 68%|████████████████████████████             | 342/500 [00:04<00:01, 84.49it/s]


100%|█████████████████████████████████████████| 500/500 [00:05<00:00, 84.46it/s]

100%|█████████████████████████████████████████| 500/500 [00:05<00:00, 84.42it/s]

 41%|████████████████▉                        | 207/500 [00:02<00:03, 84.30it/s]


100%|█████████████████████████████████████████| 500/500 [00:05<00:00, 84.59it/s]

100%|█████████████████████████████████████████| 500/500 [00:05<00:00, 84.07it/s]

 14%|██████                                    | 72/500 [00:00<00:05, 84.32it/s]


...

100%|█████████████████████████████████████████| 500/500 [00:12<00:00, 39.48it/s]

 18%|███████▍                                  | 88/500 [00:02<00:10, 39.36it/s]


 95%|███████████████████████████████████████  | 476/500 [00:12<00:00, 39.35it/s]


100%|█████████████████████████████████████████| 500/500 [00:12<00:00, 39.45it/s]

 72%|█████████████████████████████▌           | 360/500 [00:09<00:03, 39.34it/s]


100%|███████████████████████████████████████████| 16/16 [10:27<00:00, 39.24s/it]


testing:
[[1.19719016 0.49874064 0.         0.        ]]
[[1.20333533 0.50341276 0.         0.        ]]
[[1.19630857 0.49727422 0.         0.        ]]
[[1.20976748 0.4920409  0.         0.        ]]
[[1.20306217 0.49506583 0.         0.        ]]
[[1.19317939 0.4922075  0.         0.        ]]
[[1.19393165 0.4973745  0.         0.        ]]
[[1.2067589  0.49192197 0.         0.        ]]
[[1.20953522 0.50209691 0.         0.        ]]
[[1.19565614 0.49240393 0.         0.        ]]
The average mean square error is  0.017055096032568353
